In [1]:
import sys
cpath = !pwd
sys.path.append('/usr/src/app/algorithms/')
sys.path.append('/usr/src/app/')

In [2]:
from lionforests import LionForests
from algorithms.simpleSurrogate import GlobalSurrogateTree, LocalSurrogateTree
from algorithms.DefragTrees.defragTrees import DefragModel
from CHIRPS.structures import data_container
import CHIRPS.routines as rt
import CHIRPS.structures as strcts
from algorithms.anchor.anchor_tabular import AnchorTabularExplainer

from scipy import sparse

from datasets.dataset import Dataset
from sklearn.preprocessing import StandardScaler, MinMaxScaler
import pandas as pd 
import numpy as np
np.seterr(invalid='ignore')
import warnings
warnings.filterwarnings("ignore")
import time

from sklearn.model_selection import train_test_split, LeaveOneOut
from sklearn.metrics import f1_score, precision_score

abalone = Dataset()

In [3]:
X, y, feature_names, class_names = abalone.load_abalone(type='classification',ys='reduced')

In [4]:
y = [int(i) for i in y]
y = np.array(y)

In [8]:
def measure(X_train, X_test, y_train, y_test, feature_names, class_names, random_state=10):
    parameters = [{
        'max_depth': [10],
        'max_features': [0.75],
        'bootstrap': [True],
        'min_samples_leaf' : [10],
        'n_estimators': [10]
    }]
    lf = LionForests(None, False, None, feature_names, class_names)
    lf.fit(X_train, y_train, params=parameters)    
    train = lf.utilizer.transform(X_train)
    test = lf.utilizer.transform(X_test)

    predictions = lf.model.predict(train)
    test_predictions = lf.model.predict(test)
    
    def techniques(model, train, y_train, predictions, test, feature_names, class_names, lf, task, random_state=10):

        #BaselineTechnique ==============================================================================
        gt = GlobalSurrogateTree(train, predictions, feature_names, task, random_state)
        lt = LocalSurrogateTree(train, predictions, feature_names, task, 150, random_state)

        #DefragTechnique ================================================================================
        Kmax = 10
        splitter = DefragModel.parseSLtrees(model) # parse sklearn tree ensembles into the array of (feature index, threshold)
        mdl = DefragModel(modeltype=task, maxitr=100, qitr=0, tol=1e-6, restart=20, verbose=0, seed=random_state)
        mdl.fit(train, predictions, splitter, Kmax, fittype='FAB', featurename=feature_names)
        def def_cov(instances):
            ts = time.time()
            score, cover, coll = mdl.evaluate(instances[1:],lf.model.predict(instances[1:]))
            def_predictions = mdl.predict(instances[1:])
            length, nodes = mdl.find_rule_length(instances[0])
            max_len = len(length)
            comp = {1:'>',0:'<='}
            rules = {}
            for f in feature_names:
                rules[f] = []
            counter = 0
            for rule, node in list(zip(mdl.rule_,nodes)):
                for conj in range(len(node)):
                    if node[conj] and counter<=max_len-1:
                        rules[feature_names[int(rule[conj][0]-1)]].append([comp[int(rule[conj][1])],rule[conj][2]])
                        counter += 1
            new_rules = {}
            for k, v in rules.items():
                if len(v) == 1:
                    new_rules[k] = v
                else:
                    mmin = None
                    mmax = None
                    for value in v:
                        if value[0]=='<=':
                            if mmin is None or mmin > value[1]:
                                mmin = value[1]
                        if value[0]=='>':
                            if mmax is None or mmax < value[1]:
                                mmax = value[1]
                    if mmin is not None:
                        new_rules[k] = [['<=', mmin]]
                    if mmax is not None:
                        new_rules[k] = [['>', mmax]]
            te = time.time()
            #print(mdl)
            return length, cover, def_predictions, te-ts, new_rules

        #Anchors =======================================================================================
        explainer = AnchorTabularExplainer(class_names, feature_names, train)
        def anchors_method(instance):
            exp = explainer.explain_instance(instance, lf.model.predict, threshold=0.95, random_state=random_state)
            anchors_dict = {}
            for i in exp.names():
                terms = i.split(' ')
                if len(terms) == 3:
                    anchors_dict[terms[0]] = [[terms[1],float(terms[2])]]
                else:
                    anchors_dict[terms[2]] = [[terms[3],float(terms[4])],[terms[1],float(terms[0])]]
            return anchors_dict, 0

        #CHIRPS =======================================================================================
        project_dir = 'C:\\Users\\iamollas\\Downloads\\LionForests Journal\\algorithms\\CHIRPS'
        temp_y = np.array([int(i+1) for i in y_train])
        temp_frame = pd.DataFrame(np.hstack((train,temp_y.reshape(len(temp_y),1))),columns=feature_names+['class'])
        temp_frame['class']=temp_frame['class'].astype(int)
        mydata = data_container(
                data = temp_frame, class_col = 'class', var_names = feature_names,
                project_dir = project_dir, save_dir = 'abalon', random_state=random_state)
        meta_data = mydata.get_meta()
        f_walker = strcts.classification_trees_walker(forest=model, meta_data=meta_data)
        f_walker.forest_walk(instances = test, labels = model.predict(test), forest_walk_async = False)

        explanations = strcts.CHIRPS_container(f_walker.path_detail,
                                        forest=model,
                                        sample_instances=sparse.csr_matrix(train), # any representative sample can be used
                                        sample_labels=predictions,
                                        meta_data=meta_data)
        chts = time.time()
        explanations.run_explanations(target_classes=model.predict(test), # we're explaining the prediction, not the true label!
                                explanation_async=False,
                                random_state=random_state,
                                which_trees='majority',
                                alpha_paths=0.0,
                                support_paths=0.1,
                                score_func=1,
                                precis_threshold=0.99,
                                disc_path_bins=4,
                                merging_bootstraps=20,
                                pruning_bootstraps=20,
                                delta=0.2,
                                weighting='kldiv')
        chte = (time.time() - chts)/len(test)
        def chirps_method(idx):
            chirps_dict = {}
            for i in explanations.explainers[idx].pruned_rule:
                if i[1]:
                    chirps_dict[i[0]] = [['<=',float(i[2])]]
                else:
                    chirps_dict[i[0]] = [['>',float(i[2])]]
            return chirps_dict, 0, chte

        #LionForests
        def lf_rule(instance):
            temp = lf.explain(instance, reduction=True, ar_algorithm='fpgrowth', cl_algorithm='kmedoids', method='123', instance_random_state=random_state)[-1]
            rule = {}
            for key,value in temp.items():
                rule[key] = [['<=',value[1]],['>',value[0]]]
            return rule

        return {'gs':gt.rule,'ls':lt.rule,'an':anchors_method,'lf':lf_rule, 'df': def_cov, 'ch':chirps_method}
    interpretation = techniques(lf.model, train, y_train, predictions, test, feature_names, class_names, lf, 'classification', random_state)
    def rule_cov(instance, feature_names, rule):
        covered = True
        for k in range(len(instance)):
            feature = feature_names[k]
            if feature in rule.keys():
                if len(rule[feature]) == 2:
                    if instance[k] > rule[feature][0][1]: #<=
                        return 0
                    if instance[k] <= rule[feature][1][1]:#THIS <=
                        return 0
                elif rule[feature][0][0] == '>':
                    if instance[k] <= rule[feature][0][1]:
                        return 0
                else:
                    if instance[k] > rule[feature][0][1]: #<=
                        return 0
        return 1
    def rule_cov_LF(instance, feature_names, rule):
        covered = True
        for k in range(len(instance)):
            feature = feature_names[k]
            if feature in rule.keys():
                if len(rule[feature]) == 2:
                    if instance[k] > rule[feature][0][1]: #<=
                        return 0
                    if instance[k] < rule[feature][1][1]:#THIS <=
                        return 0
                elif rule[feature][0][0] == '>':
                    if instance[k] <= rule[feature][0][1]:
                        return 0
                else:
                    if instance[k] > rule[feature][0][1]: #<=
                        return 0
        return 1

    gt = GlobalSurrogateTree(train,lf.model.predict(train),feature_names,'c')
    lt = LocalSurrogateTree(train,lf.model.predict(train),feature_names,'c',150)

    rule_generator = interpretation
    full_coverage = {'gs':0, 'ls':0, 'an':0, 'lf':0, 'df':0, 'ch': 0}
    rule_length = {'gs':0, 'ls':0, 'an':0, 'lf':0, 'df':0, 'ch': 0}
    f_precision = {'gs':[], 'ls':[], 'an':[], 'lf':[], 'df':[], 'ch':[]}
    time_response = {'gs':[], 'ls':[], 'an':[], 'lf':[], 'df':[], 'ch':[]}
    rules = {'gs':[], 'ls':[], 'an':[], 'lf':[], 'df':[], 'ch':[]}

    x_train_temp = train
    x_test_temp = test

    y_train_temp = predictions
    y_test_temp = test_predictions
    
    x_train_temp_lf = lf.utilizer.inverse_transform(x_train_temp)
    x_test_temp_lf = lf.utilizer.inverse_transform(x_test_temp)  
    
    ktime = time.time()
    for test_ind in range(len(test)):
        if test_ind % 100 ==0:
            print(round(test_ind/(len(test))*100,2),'in:', time.time()-ktime)
            ktime = time.time()
            
        for name, method in rule_generator.items():
            if name == 'ch':
                rule, op, te = method(test_ind)
                coverage = 0
                precision = []
                co = 0
                for i in x_test_temp:
                    res = rule_cov(i, feature_names, rule)
                    coverage = coverage + res
                    if res == 1:
                        precision.append([y_test_temp[test_ind], y_test_temp[co]])
                    co = co + 1
                if len(precision) > 1:
                    precision = np.array(precision)
                    f_precision[name].append(precision_score(precision[:,:1],precision[:,1:],average='micro'))
                full_coverage[name] = full_coverage[name] + coverage/len(x_test_temp)
                rules['ch'].append(rule)
            elif name == 'df':
                #FIX RULE LENGTH!
                rule, cover, predictions, te, new_rules = method(np.concatenate((x_test_temp[test_ind:test_ind+1],x_test_temp)))
                f_precision[name].append(precision_score(predictions,y_test_temp,average='micro'))
                full_coverage[name] = full_coverage[name] + cover
                rules['df'].append(new_rules)
            elif name == 'lf':
                ts = time.time()
                rule = method(x_test_temp_lf[test_ind])
                te = time.time() - ts
                coverage = 0
                precision = []
                co = 0
                for i in x_test_temp_lf:
                    res = rule_cov_LF(i, feature_names, rule)
                    coverage = coverage + res
                    if res == 1:
                        precision.append([y_test_temp[test_ind], y_test_temp[co]])
                    co = co + 1
                if len(precision) > 1:
                    precision = np.array(precision)
                    f_precision[name].append(precision_score(precision[:,:1],precision[:,1:],average='micro'))
                full_coverage[name] = full_coverage[name] + coverage/len(x_test_temp_lf)
                rules['lf'].append(rule)
            else:
                ts = time.time()
                rule, prediction = method(x_test_temp[test_ind])
                te = time.time() - ts
                coverage = 0
                precision = []
                co = 0 
                for i in x_test_temp:
                    if name == 'anchors':
                        res = rule_cov(i, feature_names, rule)
                    else:    
                        res = rule_cov(i, feature_names, rule)
                    coverage = coverage + res
                    if res == 1 and name=='anchors':
                        precision.append([y_test_temp[test_ind], y_test_temp[co]])
                    elif res == 1:
                        precision.append([prediction, y_test_temp[co]])
                    co = co + 1
                if len(precision) >= 1:
                    precision = np.array(precision)
                    f_precision[name].append(precision_score(precision[:,:1],precision[:,1:],average='micro'))
                full_coverage[name] = full_coverage[name] + coverage/len(x_test_temp)
                rules[name].append(rule)
            time_response[name].append(te)
            rule_length[name] = rule_length[name] + len(rule)
    return rule_generator, full_coverage, rule_length, f_precision, time_response, rules

In [9]:
total_results2 = []
test_size_2 = []
for rand in [7, 10, 77]: #7
    total_results = []
    test_size = []
    X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, stratify=y, random_state=7)
    results = measure(X_train, X_test, y_train, y_test, feature_names, class_names, random_state=rand)
    total_results.append(results)
    test_size.append(len(X_test))
    test_size_2.append(test_size)
    total_results2.append(total_results)

len self.path_detail
806
Working on CHIRPS for instance 0 of 806
as_chirps for batch_idx 0
start mining for batch_idx 0 with support = 0.1
reduced 1273 patterns out of 6430 by numeric redundancy
found 5157 patterns from 10 trees for batch_idx 0
start score sort for batch_idx 0 (5157) patterns
start merge rule for batch_idx 0 (5157) patterns
[('Whole', False, 0.04328), ('Height', True, 0.53191), ('Viscera', False, 0.04382)]
0.924907063197026 0.37420208491194235 0.006037007405973491 0.012767897856815855
merge complete for batch_idx 0 (5157) patterns
start get explainer for batch_idx 0
as_chirps for batch_idx 1
start mining for batch_idx 1 with support = 0.1
reduced 1499 patterns out of 5434 by numeric redundancy
found 3935 patterns from 7 trees for batch_idx 1
start score sort for batch_idx 1 (3935) patterns
start merge rule for batch_idx 1 (3935) patterns
[('Shell', True, 0.4191)]
0.8363988383349468 0.41954515650871643 0.13722119105953823 0.1538599319362416
merge complete for batch_idx 

start merge rule for batch_idx 16 (6429) patterns
[('Shell', True, 0.25047)]
0.8861209964412812 0.3028888225554203 0.013437238516412058 0.02538643800067402
merge complete for batch_idx 16 (6429) patterns
start get explainer for batch_idx 16
as_chirps for batch_idx 17
start mining for batch_idx 17 with support = 0.1
reduced 370 patterns out of 1690 by numeric redundancy
found 1320 patterns from 8 trees for batch_idx 17
start score sort for batch_idx 17 (1320) patterns
start merge rule for batch_idx 17 (1320) patterns
[('Shucked', True, 0.4083), ('Shell', False, 0.39019), ('Whole', False, 0.4342)]
0.8297872340425532 0.027758601595757344 0.059262599602792884 0.07403314917127071
merge complete for batch_idx 17 (1320) patterns
start get explainer for batch_idx 17
as_chirps for batch_idx 18
start mining for batch_idx 18 with support = 0.1
reduced 1005 patterns out of 3892 by numeric redundancy
found 2887 patterns from 9 trees for batch_idx 18
start score sort for batch_idx 18 (2887) patterns

start merge rule for batch_idx 32 (2212) patterns
[('Shell', True, 0.53572)]
0.8015903067020068 0.38011756331657137 0.06344923780808057 0.10222699221895012
merge complete for batch_idx 32 (2212) patterns
start get explainer for batch_idx 32
as_chirps for batch_idx 33
start mining for batch_idx 33 with support = 0.1
reduced 1031 patterns out of 3802 by numeric redundancy
found 2771 patterns from 7 trees for batch_idx 33
start score sort for batch_idx 33 (2771) patterns
start merge rule for batch_idx 33 (2771) patterns
[('Shell', True, 0.4891)]
0.8155102040816327 0.4087493845019505 0.05696080818193669 0.07388271764401617
merge complete for batch_idx 33 (2771) patterns
start get explainer for batch_idx 33
as_chirps for batch_idx 34
start mining for batch_idx 34 with support = 0.1
reduced 42 patterns out of 263 by numeric redundancy
found 221 patterns from 7 trees for batch_idx 34
start score sort for batch_idx 34 (221) patterns
start merge rule for batch_idx 34 (221) patterns
[('Shell', T

start merge rule for batch_idx 48 (4128) patterns
[('Shell', True, 0.16106), ('Shell', False, 0.11788)]
0.9806763285024155 0.06292622442653441 0.01009522965833136 0.024831031442847477
merge complete for batch_idx 48 (4128) patterns
start get explainer for batch_idx 48
as_chirps for batch_idx 49
start mining for batch_idx 49 with support = 0.1
reduced 36 patterns out of 134 by numeric redundancy
found 98 patterns from 7 trees for batch_idx 49
start score sort for batch_idx 49 (98) patterns
start merge rule for batch_idx 49 (98) patterns
[('Shell', False, 0.58038), ('Shucked', True, 0.5243), ('Whole', False, 0.56621), ('Height', False, 0.6622340232133865)]
0.46511627906976744 0.012017224386863012 0.6183175572136739 0.7018633540372683
merge complete for batch_idx 49 (98) patterns
start get explainer for batch_idx 49
Working on CHIRPS for instance 50 of 806
as_chirps for batch_idx 50
start mining for batch_idx 50 with support = 0.1
reduced 1561 patterns out of 3837 by numeric redundancy
fo

start merge rule for batch_idx 64 (1889) patterns
[('Shell', False, 0.48551), ('Height', False, 0.62766)]
0.6428571428571429 0.179675363050838 0.02388055471060852 0.026604729729728927
merge complete for batch_idx 64 (1889) patterns
start get explainer for batch_idx 64
Working on CHIRPS for instance 65 of 806
as_chirps for batch_idx 65
start mining for batch_idx 65 with support = 0.1
reduced 526 patterns out of 2740 by numeric redundancy
found 2214 patterns from 7 trees for batch_idx 65
start score sort for batch_idx 65 (2214) patterns
start merge rule for batch_idx 65 (2214) patterns
[('Shucked', True, 0.43829), ('Whole', False, 0.45425)]
0.8727272727272727 0.03272089150443962 0.025708709672103806 0.03897032534858578
merge complete for batch_idx 65 (2214) patterns
start get explainer for batch_idx 65
as_chirps for batch_idx 66
start mining for batch_idx 66 with support = 0.1
reduced 127 patterns out of 1372 by numeric redundancy
found 1245 patterns from 6 trees for batch_idx 66
start s

...

/usr/local/lib/python3.7/site-packages/sklearn/model_selection/_validation.py:552: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "/usr/local/lib/python3.7/site-packages/sklearn/model_selection/_validation.py", line 531, in _fit_and_score
    estimator.fit(X_train, y_train, **fit_params)
  File "/usr/local/lib/python3.7/site-packages/sklearn/tree/_classes.py", line 1246, in fit
    X_idx_sorted=X_idx_sorted)
  File "/usr/local/lib/python3.7/site-packages/sklearn/tree/_classes.py", line 336, in fit
    criterion = CRITERIA_REG[self.criterion](self.n_outputs_,
KeyError: 'poisson'

  FitFailedWarning)
/usr/local/lib/python3.7/site-packages/sklearn/model_selection/_validation.py:552: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "/usr/local/li

  File "/usr/local/lib/python3.7/site-packages/sklearn/model_selection/_validation.py", line 531, in _fit_and_score
    estimator.fit(X_train, y_train, **fit_params)
  File "/usr/local/lib/python3.7/site-packages/sklearn/tree/_classes.py", line 1246, in fit
    X_idx_sorted=X_idx_sorted)
  File "/usr/local/lib/python3.7/site-packages/sklearn/tree/_classes.py", line 336, in fit
    criterion = CRITERIA_REG[self.criterion](self.n_outputs_,
KeyError: 'poisson'

  FitFailedWarning)
/usr/local/lib/python3.7/site-packages/sklearn/model_selection/_validation.py:552: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "/usr/local/lib/python3.7/site-packages/sklearn/model_selection/_validation.py", line 531, in _fit_and_score
    estimator.fit(X_train, y_train, **fit_params)
  File "/usr/local/lib/python3.7/site-packages/sklearn/tree/_classes.py", line 1246, in fit
    X_idx_s

  File "/usr/local/lib/python3.7/site-packages/sklearn/model_selection/_validation.py", line 531, in _fit_and_score
    estimator.fit(X_train, y_train, **fit_params)
  File "/usr/local/lib/python3.7/site-packages/sklearn/tree/_classes.py", line 1246, in fit
    X_idx_sorted=X_idx_sorted)
  File "/usr/local/lib/python3.7/site-packages/sklearn/tree/_classes.py", line 336, in fit
    criterion = CRITERIA_REG[self.criterion](self.n_outputs_,
KeyError: 'poisson'

  FitFailedWarning)
/usr/local/lib/python3.7/site-packages/sklearn/model_selection/_validation.py:552: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "/usr/local/lib/python3.7/site-packages/sklearn/model_selection/_validation.py", line 531, in _fit_and_score
    estimator.fit(X_train, y_train, **fit_params)
  File "/usr/local/lib/python3.7/site-packages/sklearn/tree/_classes.py", line 1246, in fit
    X_idx_s

/usr/local/lib/python3.7/site-packages/sklearn/model_selection/_validation.py:552: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "/usr/local/lib/python3.7/site-packages/sklearn/model_selection/_validation.py", line 531, in _fit_and_score
    estimator.fit(X_train, y_train, **fit_params)
  File "/usr/local/lib/python3.7/site-packages/sklearn/tree/_classes.py", line 1246, in fit
    X_idx_sorted=X_idx_sorted)
  File "/usr/local/lib/python3.7/site-packages/sklearn/tree/_classes.py", line 336, in fit
    criterion = CRITERIA_REG[self.criterion](self.n_outputs_,
KeyError: 'poisson'

  FitFailedWarning)
/usr/local/lib/python3.7/site-packages/sklearn/model_selection/_validation.py:552: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "/usr/local/li

0.0 in: 3.4809112548828125e-05
12.41 in: 1544.1218943595886
24.81 in: 1325.293935060501
37.22 in: 1480.647411108017
49.63 in: 1359.4619410037994
62.03 in: 1365.91006398201
74.44 in: 1558.737096786499
86.85 in: 1480.9490630626678
99.26 in: 1406.4547951221466


In [10]:
from utilities.lionforests_utility import path_similarity
rule_variance = {'gs':[], 'ls':[], 'an':[], 'lf':[], 'df':[], 'ch': []}


folds = 0
test_size = []
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, stratify=y, random_state=7)

min_max_feature_values = {}
for i in range(len(feature_names)):
        min_max_feature_values[feature_names[i]] = [min(X_train[:, i]), max(X_train[:, i])] 
for name in ['gs', 'ls', 'an', 'lf', 'df', 'ch']:
    for k in range(len(total_results2[0][folds][-1][name])):
        r1 = total_results2[0][0][-1][name][k]
        r2 = total_results2[1][0][-1][name][k]
        r3 = total_results2[2][0][-1][name][k]
        #try:
        rule_variance[name].append((path_similarity(r1, r2, feature_names, min_max_feature_values)+
                                       path_similarity(r1, r3, feature_names, min_max_feature_values)+
                                       path_similarity(r2, r3, feature_names, min_max_feature_values))/3)

In [11]:
f_full_coverage = {'gs':[], 'ls':[], 'an':[], 'lf':[], 'df':[], 'ch': []}
f_rule_length = {'gs':[], 'ls':[], 'an':[], 'lf':[], 'df':[], 'ch': []}
f_f_precision = {'gs':[], 'ls':[], 'an':[], 'lf':[], 'df':[], 'ch':[]}
f_f_time = {'gs':[], 'ls':[], 'an':[], 'lf':[], 'df':[], 'ch':[]}
for b in range(3):
    full_coverage = {'gs':[], 'ls':[], 'an':[], 'lf':[], 'df':[], 'ch': []}
    rule_length = {'gs':[], 'ls':[], 'an':[], 'lf':[], 'df':[], 'ch': []}
    f_precision = {'gs':[], 'ls':[], 'an':[], 'lf':[], 'df':[], 'ch':[]}
    f_time = {'gs':[], 'ls':[], 'an':[], 'lf':[], 'df':[], 'ch':[]}
    k = 0
    for i in total_results2[b]:
        for name, method in i[0].items():
            full_coverage[name].append(i[1][name]/test_size_2[b][k])
            rule_length[name].append(i[2][name]/test_size_2[b][k])
            f_precision[name].append(np.array(i[3][name]).mean())
            f_time[name].append(np.array(i[4][name]).mean())
        k = + 1
    for name, method in i[0].items():
        f_full_coverage[name].append(np.array(full_coverage[name]).mean())
        f_rule_length[name].append(np.array(rule_length[name]).mean())
        f_f_precision[name].append(np.array(f_precision[name]).mean())
        f_f_time[name].append(np.array(f_time[name]).mean())
for name, method in i[0].items():
    print(name,  '| %5.4f  %5.3f | %5.4f %5.3f | %5.4f  %5.3f | %5.4f  %5.3f | %5.4f  %5.3f' 
          % (np.array(f_full_coverage[name]).mean(),np.array(f_full_coverage[name]).std(),
             np.array(f_rule_length[name]).mean(),np.array(f_rule_length[name]).std(),
             np.array(f_f_precision[name]).mean(),np.array(f_f_precision[name]).std(),
             np.array(f_f_time[name]).mean(),np.array(f_f_time[name]).std(),
             np.array(rule_variance[name]).mean(),np.array(rule_variance[name]).std()))

gs | 0.0766  0.000 | 3.6042 0.033 | 0.9061  0.003 | 0.0003  0.000 | 0.9244  0.122
ls | 0.2499  0.003 | 2.3342 0.023 | 0.8103  0.002 | 2.1120  0.009 | 0.7182  0.189
an | 0.1064  0.003 | 3.5029 0.055 | 0.0296  0.000 | 11.0825  0.610 | 0.8560  0.181
lf | 0.0018  0.000 | 6.7957 0.002 | 1.0000  0.000 | 0.3438  0.006 | 0.9494  0.087
df | 0.9921  0.001 | 12.1935 0.904 | 0.7568  0.002 | 0.1385  0.004 | 0.7054  0.067
ch | 0.3485  0.004 | 2.1117 0.002 | 0.8800  0.002 | 5.6240  0.103 | 0.9179  0.104


In [12]:
import csv  

with open('abalone mc.csv', 'w', encoding='UTF8') as f:
    writer = csv.writer(f)
    for name, method in i[0].items():
        writer.writerow([name, np.array(f_full_coverage[name]).mean(),np.array(f_full_coverage[name]).std(),
             np.array(f_rule_length[name]).mean(),np.array(f_rule_length[name]).std(),
             np.array(f_f_precision[name]).mean(),np.array(f_f_precision[name]).std(),
             np.array(f_f_time[name]).mean(),np.array(f_f_time[name]).std(),
             np.array(rule_variance[name]).mean(),np.array(rule_variance[name]).std()])